<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## Data Processing Workflow

In this workflow within PyCCAPT, we can crop the data, do the voltage and bowl calibration, calculate the 3d reconstruction, and do the ranging.
</div>

In [1]:
# Activate intractive functionality of matplotlib
%matplotlib ipympl
# Activate auto reload 
%load_ext autoreload
%autoreload 2
%reload_ext autoreload
# import libraries
import os
import numpy as np
import pandas as pd
import subprocess
from ipywidgets import widgets
from IPython.display import display
from ipywidgets import fixed, interact_manual
import warnings
# Ignore all warnings
warnings.filterwarnings("ignore")

# Local module and scripts
from pyccapt.calibration.calibration import widgets as wd
from pyccapt.calibration.data_tools import data_tools, data_loadcrop
from pyccapt.calibration.tutorials.tutorials_helpers import helper_calibration
from pyccapt.calibration.tutorials.tutorials_helpers import helper_data_loader
from pyccapt.calibration.tutorials.tutorials_helpers import helper_temporal_crop
from pyccapt.calibration.tutorials.tutorials_helpers import helper_special_crop
from pyccapt.calibration.tutorials.tutorials_helpers import helper_t_0_tune
from pyccapt.calibration.tutorials.tutorials_helpers import helper_mc_plot
from pyccapt.calibration.tutorials.tutorials_helpers import helper_3d_reconstruction
from pyccapt.calibration.tutorials.tutorials_helpers import helper_ion_selection
from pyccapt.calibration.tutorials.tutorials_helpers import helper_visualization
from pyccapt.calibration.tutorials.tutorials_helpers import helper_ion_list
from pyccapt.calibration.calibration import ion_selection
from pyccapt.calibration.calibration import share_variables
from pyccapt.calibration.leap_tools.leap_tools import read_rrng

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
In case of recieving the error about pytable library, you have to install the pytables library with conda command. to do that you can open a new cell and copy the line below in it. Then just run it like other cells. The pytables library will be innstalled.
    
`!conda install --yes --prefix {sys.prefix} pytables`
</div>


<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
In the cell below we create variable object. This object is used in many of the functions to share the data between functions in as easy way. 
</div>


In [2]:
variables = share_variables.Variables()

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
    
By clicking on the button below, you can select the dataset file you want to work with. The dataset file can be in various formats, including HDF5, EPOS, POS, ATO, and CSV. The cropped data will be saved in the same directory as the original dataset file in a new directory nammed load_crop. The name of the cropped dataset file will be the same as the original dataset file. The figures will be saved in the same directory as the dataset file.
</div>

In [3]:
button = widgets.Button(description='load dataset')

@button.on_click
def open_file_on_click_r(b):
    global dataset_path
    folder_path = variables.last_directory
    script = '..//..//data_tools//run_dataset_path_qt.py'
    cmd = f"python {script} {folder_path}"
    result = subprocess.run(cmd, capture_output=True, text=True, shell=True)
    dataset_path = result.stdout.strip()
    variables.last_directory = dataset_path

button

Button(description='load dataset', style=ButtonStyle())

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## ROI Selection and Data Cropping
    

</div>



<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

    
From the dropdown lists below, you can select the instrument specifications of the dataset. The instrument specifications are the same as the ones used for the calibration process. Data mode is specify the dataset structure. The dataset can be in raw or calibrated mode. The flight path length is the distance between the sample and the detector. The t0 is the time of flight of the ions with the lowest mass-to-charge ratio. The maximum mass-to-charge ratio is the maximum mass-to-charge ratio of tat you want to plot. You can also change it in te related cells. The detector diameter is the diameter of the detector.
</div>


In [4]:
# create an object for selection of instrument specifications of the dataset
tdc, pulse_mode, flight_path_length, t0, max_mc, det_diam = wd.dataset_instrument_specification_selection()

# Display lists and comboboxes to selected instrument specifications
display(tdc, pulse_mode, flight_path_length, t0, det_diam, max_mc)

Dropdown(description='Data mode:', options=('pyccapt', 'leap_epos', 'leap_pos', 'leap_apt', 'ato_v6'), value='…

Dropdown(description='Pulse mode:', options=('voltage', 'laser'), value='voltage')

FloatText(value=110.0, description='Flight path length:')

FloatText(value=38.0, description='t0:')

FloatText(value=80.0, description='Detector diameter:')

FloatText(value=400.0, description='Max mc:')

In [11]:
helper_data_loader.load_data(dataset_path, max_mc.value, flight_path_length.value, pulse_mode.value, tdc.value, variables)
data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)
display(variables.data)
display(variables.range_data)

The maximum possible TOF is: 5010 ns
The data will be saved on the path: T:/Monajem/APT_data/Nimonic_Benedict/2470_Apr-17-2025_13-10_NiC2_Nimonic90_HT_HPCF_1/data_processing/
The dataset name after saving is: 2470_Apr-17-2025_13-10_NiC2_Nimonic90_HT_HPCF_1
The figures will be saved on the path: T:/Monajem/APT_data/Nimonic_Benedict/2470_Apr-17-2025_13-10_NiC2_Nimonic90_HT_HPCF_1/data_processing/
{'apt': ['experiment_chamber_vacuum', 'id', 'num_events', 'num_raw_signals', 'temperature', 'timestamps'], 'dld': ['high_voltage', 'laser_pulse', 'start_counter', 't', 'voltage_pulse', 'x', 'y'], 'tdc': ['channel', 'high_voltage', 'laser_pulse', 'start_counter', 'time_data', 'voltage_pulse']}
The data is loaded in raw mode
The number of data that is removed: 609109
Total number of Ions: 4798949
The maximum possible time of flight is: 5010


x (nm)  y (nm)  z (nm)  mc (Da)  mc_uc (Da)  high_voltage (V)  \
0           0.0     0.0     0.0      0.0         0.0             500.0   
1           0.0     0.0     0.0      0.0         0.0             500.0   
2           0.0     0.0     0.0      0.0         0.0             500.0   
3           0.0     0.0     0.0      0.0         0.0             500.0   
4           0.0     0.0     0.0      0.0         0.0             500.0   
...         ...     ...     ...      ...         ...               ...   
4798944     0.0     0.0     0.0      0.0         0.0            8000.0   
4798945     0.0     0.0     0.0      0.0         0.0            8000.0   
4798946     0.0     0.0     0.0      0.0         0.0            8000.0   
4798947     0.0     0.0     0.0      0.0         0.0            8000.0   
4798948     0.0     0.0     0.0      0.0         0.0            8000.0   

         pulse_v (V)  pulse_l (pJ)       t (ns)  t_c (ns)  x_det (cm)  \
0              328.0           0.0  2363.698854       0.0    3.121633   
1              328.0           0.0  3814.824222       0.0   -1.475918   
2              328.0           0.0  4559.897916       0.0    3.007347   
3              328.0           0.0   616.493052       0.0    3.242449   
4              328.0           0.0   282.926790       0.0    3.363265   
...              ...           ...          ...       ...         ...   
4798944       1600.0           0.0  1957.190904       0.0    3.121633   
4798945       1600.0           0.0  1799.278596       0.0    0.385306   
4798946       1600.0           0.0  4288.156524       0.0    1.518367   
4798947       1600.0           0.0   500.880888       0.0   -2.047347   
4798948       1600.0           0.0  1925.472654       0.0    1.577143   

         y_det (cm)  delta_p  multi  start_counter  
0          0.009796      0.0    0.0           3269  
1         -1.760000      0.0    0.0           5738  
2         -0.362449      0.0    0.0           7933  
3         -1.835102      0.0    0.0          10955  
4          0.277551      0.0    0.0           1558  
...             ...      ...    ...            ...  
4798944   -0.796735      0.0    0.0          10945  
4798945   -2.481633      0.0    0.0           2057  
4798946   -3.137959      0.0    0.0           3558  
4798947   -3.072653      0.0    0.0           4570  
4798948    3.075918      0.0    0.0           4761  

[4798949 rows x 15 columns]

name ion  mass   mc  mc_low  mc_up    color     element complex  \
0  unranged0  un   0.0  0.0     0.0  400.0  #000000  [unranged]     [0]   

  isotope  charge  
0     [0]       0

<div style="margin: 0 auto; padding: 20px;">

Load a pre saved range file if you want from cell below
</div>


In [12]:
button_r = widgets.Button(description='load range dataset')

@button_r.on_click
def open_file_on_click_r(b):
    global range_path
    folder_path = variables.last_directory
    script = '..//..//data_tools//run_dataset_path_qt.py'
    cmd = f"python {script} {folder_path}"
    result = subprocess.run(cmd, capture_output=True, text=True, shell=True)
    range_path = result.stdout.strip()
    variables.last_directory = range_path

button_r

Button(description='load range dataset', style=ButtonStyle())

In [13]:
if 'range_path' in globals():
    _, file_extension = os.path.splitext(range_path)
    if file_extension == '.rrng':
        variables.range_data = read_rrng(range_path)
    else:
        variables.range_data = pd.read_hdf(range_path, mode='r')
display(variables.range_data)

name ion  mass   mc  mc_low  mc_up    color     element complex  \
0  unranged0  un   0.0  0.0     0.0  400.0  #000000  [unranged]     [0]   

  isotope  charge  
0     [0]       0

<div style="margin: 0 auto; padding: 20px;">

# Temporal crop

Select the data by drawing a rectangle over the experiment history. Experiment history is a 2D histogram of the time of flight of the ions versus sequence of evaporation. The experiment history is plotted by clicking on the button below te cell.
</div>


In [14]:
helper_temporal_crop.call_plot_crop_experiment(variables, pulse_mode.value)

Output()

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

# Spatial crop

Select the region of maximum concentration of Ions in the below plotted graph to utilize relevant data. To crop you can draw a circle over the filed desorption map. The field desorption map is a 2D histogram of the time of flight of the ions versus the position of the ions on the detector. The field desorption map is plotted by clicking on the button below the cell.
</div>

In [15]:
helper_special_crop.call_plot_crop_fdm(variables)

Output()

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

Calculate pulses since the last event pulse and ions per pulse. The percentage of loss in ROI selection process will be printed.
</div>

In [16]:
# maximum value of the tdc counter
if tdc.value == 'pyccapt':
    if not (variables.data['delta_p'] != 0).any() or not (variables.data['multi'] != 0).any():
        if (variables.data['start_counter'] != 0).any():
            max_start_counter = max(variables.data['start_counter'])
            # if (variables.data['pulse_pi'] == 0).all() or (variables.data['ion_pp'] == 0).all():
            pulse_pi, ion_pp = data_loadcrop.calculate_ppi_and_ipp(variables.data, max_start_counter)
            # add two calculated array to the croped dataset
            variables.data['delta_p'] = pulse_pi.astype(np.uintc)
            variables.data['multi'] = ion_pp.astype(np.uintc)
    
    # save the cropped data
    print('tof Crop Loss {:.2f} %'.format((100 - (len(variables.data) / len(variables.data_backup)) * 100)))
#percentage of double event per pulse
ion_pp = variables.data['multi'].to_numpy()
print('percentage of multihit event per pulse', len(ion_pp[ion_pp != 1]) / float(len(ion_pp)) * 100)

Progress: 0% complete
Progress: 19% complete
Progress: 39% complete
Progress: 59% complete
Progress: 79% complete
Progress: 99% complete
tof Crop Loss 41.63 %
percentage of multihit event per pulse 12.253636218568303


<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

In the next cell by changing the t<sub>0</sub> value you can correct the position of H<sub>1</sub> or any other known peak. this correction would be helpful for the position of the peaks in the m/c calibration process.
</div>

In [17]:
data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)
variables.data

The maximum possible time of flight is: 5010


x (nm)  y (nm)  z (nm)  mc (Da)  mc_uc (Da)  high_voltage (V)  \
0           0.0     0.0     0.0      0.0         0.0         5265.2672   
1           0.0     0.0     0.0      0.0         0.0         5265.2672   
2           0.0     0.0     0.0      0.0         0.0         5265.1040   
3           0.0     0.0     0.0      0.0         0.0         5265.1040   
4           0.0     0.0     0.0      0.0         0.0         5265.1040   
...         ...     ...     ...      ...         ...               ...   
2801188     0.0     0.0     0.0      0.0         0.0         5978.9408   
2801189     0.0     0.0     0.0      0.0         0.0         5978.9408   
2801190     0.0     0.0     0.0      0.0         0.0         5978.9408   
2801191     0.0     0.0     0.0      0.0         0.0         5978.9408   
2801192     0.0     0.0     0.0      0.0         0.0         5978.9408   

         pulse_v (V)  pulse_l (pJ)       t (ns)  t_c (ns)  x_det (cm)  \
0         1053.05344           0.0   588.347820       0.0   -1.074286   
1         1053.05344           0.0  3904.300548       0.0    1.985306   
2         1053.02080           0.0   626.306850       0.0    0.800000   
3         1053.02080           0.0   590.501232       0.0    0.519184   
4         1053.02080           0.0   624.633498       0.0    0.933878   
...              ...           ...          ...       ...         ...   
2801188   1195.78816           0.0   555.827184       0.0   -1.413878   
2801189   1195.78816           0.0   593.162136       0.0   -1.280000   
2801190   1195.78816           0.0   567.890406       0.0    2.132245   
2801191   1195.78816           0.0   584.438760       0.0   -1.554286   
2801192   1195.78816           0.0   586.715616       0.0    1.580408   

         y_det (cm)     delta_p  multi  start_counter  
0         -1.384490           0      1          12400  
1          0.114286          97      1          12497  
2         -0.764082  4294954850      1             51  
3          0.675918          94      1            145  
4          0.878367         190      1            335  
...             ...         ...    ...            ...  
2801188   -0.313469         152      2           2474  
2801189   -0.473469           0      2           2474  
2801190    1.198367           9      1           2483  
2801191   -0.457143          96      1           2579  
2801192   -0.434286          22      1           2601  

[2801193 rows x 15 columns]

In [18]:
helper_t_0_tune.call_fine_tune_t_0(variables, flight_path_length, pulse_mode, t0)

Output()

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

Remove the data with m/c greater than max m/c and x, y, t = 0. Also add the needed colums for calibration. The data types of the final cropped dataset is displayed below.

</div>

In [19]:
# add the columns in the dataset for x, y, z, mc, mc calibrated, and t calibrated
helper_data_loader.add_columns(variables, max_mc)
# save data temporarily
data_tools.save_data(variables.data, variables, hdf=True, epos=False, pos=False, csv=False, temp=True)
display(variables.data)
display(variables.data.dtypes)

The number of data over max_mc: 0
The number of data with having t, x, and y equal to zero is: 0


x (nm)  y (nm)  z (nm)  mc (Da)   mc_uc (Da)  high_voltage (V)  \
0           0.0     0.0     0.0      0.0    28.255415         5265.2672   
1           0.0     0.0     0.0      0.0  1402.082033         5265.2672   
2           0.0     0.0     0.0      0.0    32.805438         5265.1040   
3           0.0     0.0     0.0      0.0    29.026195         5265.1040   
4           0.0     0.0     0.0      0.0    32.506151         5265.1040   
...         ...     ...     ...      ...          ...               ...   
2801188     0.0     0.0     0.0      0.0    28.603727         5978.9408   
2801189     0.0     0.0     0.0      0.0    32.974345         5978.9408   
2801190     0.0     0.0     0.0      0.0    29.045809         5978.9408   
2801191     0.0     0.0     0.0      0.0    31.741900         5978.9408   
2801192     0.0     0.0     0.0      0.0    31.993011         5978.9408   

         pulse_v (V)  pulse_l (pJ)       t (ns)  t_c (ns)  x_det (cm)  \
0         1053.05344           0.0   588.347820       0.0   -1.074286   
1         1053.05344           0.0  3904.300548       0.0    1.985306   
2         1053.02080           0.0   626.306850       0.0    0.800000   
3         1053.02080           0.0   590.501232       0.0    0.519184   
4         1053.02080           0.0   624.633498       0.0    0.933878   
...              ...           ...          ...       ...         ...   
2801188   1195.78816           0.0   555.827184       0.0   -1.413878   
2801189   1195.78816           0.0   593.162136       0.0   -1.280000   
2801190   1195.78816           0.0   567.890406       0.0    2.132245   
2801191   1195.78816           0.0   584.438760       0.0   -1.554286   
2801192   1195.78816           0.0   586.715616       0.0    1.580408   

         y_det (cm)     delta_p  multi  start_counter  
0         -1.384490           0      1          12400  
1          0.114286          97      1          12497  
2         -0.764082  4294954850      1             51  
3          0.675918          94      1            145  
4          0.878367         190      1            335  
...             ...         ...    ...            ...  
2801188   -0.313469         152      2           2474  
2801189   -0.473469           0      2           2474  
2801190    1.198367           9      1           2483  
2801191   -0.457143          96      1           2579  
2801192   -0.434286          22      1           2601  

[2801193 rows x 15 columns]

x (nm)              float64
y (nm)              float64
z (nm)              float64
mc (Da)             float64
mc_uc (Da)          float64
high_voltage (V)    float64
pulse_v (V)         float64
pulse_l (pJ)        float64
t (ns)              float64
t_c (ns)            float64
x_det (cm)          float64
y_det (cm)          float64
delta_p              uint32
multi                uint32
start_counter        uint32
dtype: object

-------------------------------------------------------
-------------------------------------------------------

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## Time-of-Flight/Mass-to-charge Calibration
</div>

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
    
Below you can plot the ToF histogram of the dataset. You can select the peak range of the data you want to plot by drawing a rectangle over peak with holding left click. After that you should apply the voltage and bowl calibration. These three steps should be repeated until you see no improvement in the peak resolution. You can also save the calibration by clicking on the save button. The saved calibration will be used for the next steps.

</div>

In [20]:
# exctract needed data from Pandas data frame as an numpy array
data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)

The maximum possible time of flight is: 5010


In [21]:
helper_calibration.call_voltage_bowl_calibration(variables, det_diam.value, flight_path_length.value, pulse_mode.value)

cannot find the maximum for i, j: 18 -27


In [22]:
variables.dld_t_calib_backup = np.copy(variables.dld_t_calib)
variables.mc_calib_backup = np.copy(variables.mc_calib)

In [23]:
helper_ion_list.call_ion_list(variables, selector='peak')

In [24]:
variables.data['mc (Da)'] = variables.mc_calib
variables.data['t_c (ns)'] = variables.dld_t_calib
# Remove negative mc
threshold = 0
mc_t = variables.data['mc (Da)'].to_numpy()
mc_t_mask = (mc_t <= threshold)
print('The number of ions with negative mc are:', len(mc_t_mask[mc_t_mask==True]))
variables.data.drop(np.where(mc_t_mask)[0], inplace=True)
variables.data.reset_index(inplace=True, drop=True)
# save data temporarily
data_tools.save_data(variables.data, variables, hdf=True, epos=False, pos=False, csv=False, temp=True)

The number of ions with negative mc are: 0


In [25]:
helper_mc_plot.call_mc_plot(variables, selector='None')

Output()

-------------------------------------------------------
-------------------------------------------------------

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## 3D Reconstruction
After bowl and voltage calibration we are ready to calculate the 3d reconstruction. In this workflow we calculate the reconstructed x,y,z and then plot the 3d, heatmap, projection plots and mass-to-charge histogram.

</div>

In [26]:
# exctract needed data from Pandas data frame as a numpy array
data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)

display(variables.data)

The maximum possible time of flight is: 5010


x (nm)  y (nm)  z (nm)      mc (Da)   mc_uc (Da)  high_voltage (V)  \
0           0.0     0.0     0.0    26.132216    28.255415         5265.2672   
1           0.0     0.0     0.0  1217.088374  1402.082033         5265.2672   
2           0.0     0.0     0.0    29.970803    32.805438         5265.1040   
3           0.0     0.0     0.0    26.107493    29.026195         5265.1040   
4           0.0     0.0     0.0    29.148887    32.506151         5265.1040   
...         ...     ...     ...          ...          ...               ...   
2801188     0.0     0.0     0.0    26.074480    28.603727         5978.9408   
2801189     0.0     0.0     0.0    30.066633    32.974345         5978.9408   
2801190     0.0     0.0     0.0    26.115901    29.045809         5978.9408   
2801191     0.0     0.0     0.0    28.958678    31.741900         5978.9408   
2801192     0.0     0.0     0.0    29.171057    31.993011         5978.9408   

         pulse_v (V)  pulse_l (pJ)       t (ns)     t_c (ns)  x_det (cm)  \
0         1053.05344           0.0   588.347820   588.347820   -1.074286   
1         1053.05344           0.0  3904.300548  3904.300548    1.985306   
2         1053.02080           0.0   626.306850   626.306850    0.800000   
3         1053.02080           0.0   590.501232   590.501232    0.519184   
4         1053.02080           0.0   624.633498   624.633498    0.933878   
...              ...           ...          ...          ...         ...   
2801188   1195.78816           0.0   555.827184   555.827184   -1.413878   
2801189   1195.78816           0.0   593.162136   593.162136   -1.280000   
2801190   1195.78816           0.0   567.890406   567.890406    2.132245   
2801191   1195.78816           0.0   584.438760   584.438760   -1.554286   
2801192   1195.78816           0.0   586.715616   586.715616    1.580408   

         y_det (cm)     delta_p  multi  start_counter  
0         -1.384490           0      1          12400  
1          0.114286          97      1          12497  
2         -0.764082  4294954850      1             51  
3          0.675918          94      1            145  
4          0.878367         190      1            335  
...             ...         ...    ...            ...  
2801188   -0.313469         152      2           2474  
2801189   -0.473469           0      2           2474  
2801190    1.198367           9      1           2483  
2801191   -0.457143          96      1           2579  
2801192   -0.434286          22      1           2601  

[2801193 rows x 15 columns]

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

You have to select the main element in your sample from the from dropdown below.
</div>

In [9]:
element_selected = wd.density_field_selection()
display(element_selected)

Dropdown(description='Element', options=((1, 'H', 52.7, 0.0), (2, 'He', 28.7, 0.0), (3, 'Li', 46.3, 14.0), (4,…

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

In case that yopu face error about plotly library, like javascripts error. You have check your jupyter lab version is compatibale with the plotly extenstion. Sometimes running `jupyter lab build` command fix the proble.
</div>

In [27]:
helper_3d_reconstruction.call_x_y_z_calculation(variables, flight_path_length, element_selected=element_selected)

Output()

In [ ]:
variables.data['x (nm)'] = variables.x
variables.data['y (nm)'] = variables.y
variables.data['z (nm)'] = variables.z
# save data temporarily
data_tools.save_data(variables.data, variables, hdf=True, epos=False, pos=False, csv=False, temp=True)

-------------------------------------------------------
-------------------------------------------------------

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## Ion Selection and Rangging

Users can choose ions using peak and element finders, manually add ions, customize ion colors, and create histograms. Histograms can be generated for selected ranges and areas, and figures can be saved. Additionally, users have the option to save both statistics and  range data.

</div>

In [ ]:
# exctract needed data from Pandas data frame as an numpy array
data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)

display(variables.data)

In [ ]:
display(variables.data.dtypes)

In [ ]:
helper_ion_selection.call_ion_selection(variables)

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

Now we can also show the color in the range dataframe

</div>

In [ ]:
display(variables.range_data.style.applymap(ion_selection.display_color, subset=['color']))

In [ ]:
variables.range_data.dtypes

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

Save the range in the hdf5 and csv format.

</div>

In [ ]:
interact_manual_range = interact_manual.options(manual_name="save range")
interact_manual_range(data_tools.save_range, variables=fixed(variables));

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

Save the cropped dataset. You can specify te output format from list below. The output formats are HDF5, EPOS, POS, ATO, and CSV. The output file will be saved in the same directory as the original dataset file in a new directory nammed load_crop.
</div>

In [35]:
interact_manual_data = interact_manual.options(manual_name="save data")
interact_manual_data(data_tools.save_data, data=fixed(variables.data), variables=fixed(variables),
                name=widgets.Text(value=variables.result_data_name),
                hdf=widgets.Dropdown(options=[('True', True), ('False', False)]),
                epos=widgets.Dropdown(options=[('False', False), ('True', True)]),
                pos=widgets.Dropdown(options=[('False', False), ('True', True)]),
                ato_6v=widgets.Dropdown(options=[('False', False), ('True', True)]),
                csv=widgets.Dropdown(options=[('False', False), ('True', True)]),
               temp=fixed(False));

interactive(children=(Text(value='2470_Apr-17-2025_13-10_NiC2_Nimonic90_HT_HPCF_1', continuous_update=False, d…

-------------------------------------------------------
-------------------------------------------------------

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
    
# Visualization
    
</div>

In [ ]:
variables.data

# helper_visualization.call_visualization(variables)

In [ ]:
data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)

In [ ]:
helper_visualization.call_visualization(variables)

In [ ]:
mask_h1 = (variables.mc <1.11) & (variables.mc > 0.89)
mask_h2 = (variables.mc <2.2) & (variables.mc > 1.87)
h1 = variables.mc[mask_h1]
h2 = variables.mc[mask_h2]
voltage = variables.dld_high_voltage

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

def plot_mc_vs_voltage_steps(variables, num_steps=100):
    """
    Plots the amount or percentage of h1 and h2 vs voltage, dividing the voltage
    range into specified steps.

    Args:
        variables: DataFrame or object with 'mc' and 'high_voltage' columns.
        num_steps: Number of steps to divide the voltage range into.
    """

    min_voltage = variables.dld_high_voltage.min()
    max_voltage = variables.dld_high_voltage.max()
    voltage_values = np.linspace(min_voltage, max_voltage, num_steps)

    h1_amounts = []
    h2_amounts = []
    h1_percentages = []
    h2_percentages = []

    for voltage in voltage_values:
        # Create a boolean mask to select data points within a small voltage range
        # around the current voltage step.
        voltage_mask = (variables.dld_high_voltage >= voltage - (max_voltage - min_voltage) / (2 * num_steps)) & \
                       (variables.dld_high_voltage <= voltage + (max_voltage - min_voltage) / (2 * num_steps))
        # voltage_data = variables[voltage_mask]
        mc_masked = variables.mc[voltage_mask]

        mask_h1 = (mc_masked < 1.11) & (mc_masked > 0.89)
        mask_h2 = (mc_masked < 2.2) & (mc_masked > 1.87)

        h1 = mc_masked[mask_h1]
        h2 = mc_masked[mask_h2]

        h1_amounts.append(len(h1))
        h2_amounts.append(len(h2))

        total_count = len(mc_masked)
        if total_count > 0:
            h1_percentages.append((len(h1) / total_count) * 100)
            h2_percentages.append((len(h2) / total_count) * 100)
        else:
            h1_percentages.append(0)
            h2_percentages.append(0)

    # Plotting amounts
    plt.figure(figsize=(10, 5))
    plt.plot(voltage_values, h1_amounts, label=r'$h_1$')
    plt.plot(voltage_values, h2_amounts, label=r'$h_2$')
    plt.xlabel('DC Voltage')
    plt.ylabel('Count')
    plt.legend()
    plt.grid(True)
    plt.show()

    # Plotting percentages
    plt.figure(figsize=(10, 5))
    plt.plot(voltage_values, h1_percentages, label=r'$H_1$')
    plt.plot(voltage_values, h2_percentages, label=r'$H_2$')
    plt.xlabel('DC Voltage')
    plt.ylabel('Percentage (%)')
    plt.legend()
    plt.grid(True)
    plt.show()

# Example usage (assuming 'variables' is your DataFrame):
plot_mc_vs_voltage_steps(variables, num_steps=200)

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

def plot_mc_vs_voltage_constant_count(variables, range_devide=1_000_000):
    """
    Plots the amount or percentage of h1 and h2 vs voltage, dividing the voltage
    range based on a constant number of data points per range.

    Args:
        variables: DataFrame or object with 'dld_high_voltage' and 'mc' columns.
        num_per_range: Number of data points per voltage range.
    """

    num_range = int(len(variables.dld_high_voltage) / range_devide)
    voltage_values = []
    h1_amounts = []
    h2_amounts = []
    h1_percentages = []
    h2_percentages = []

    for i in range(num_range):
        if i * range_devide < len(variables.dld_high_voltage):
            dld_high_voltage_masked = variables.dld_high_voltage[i:i * range_devide]
            mc_masked = variables.mc[i:i * range_devide]
        else:
            dld_high_voltage_masked = variables.dld_high_voltage[i:]
            mc_masked = variables.mc[i:]
        
        voltage = dld_high_voltage_masked.mean()  # Use mean voltage for the range

        voltage_values.append(voltage)

        mask_h1 = (mc_masked < 1.11) & (mc_masked > 0.89)
        mask_h2 = (mc_masked < 2.2) & (mc_masked > 1.87)

        h1 = mc_masked[mask_h1]
        h2 = mc_masked[mask_h2]

        h1_amounts.append(len(h1))
        h2_amounts.append(len(h2))

        total_count = len(mc_masked)
        if total_count > 0:
            h1_percentages.append((len(h1) / total_count) * 100)
            h2_percentages.append((len(h2) / total_count) * 100)
        else:
            h1_percentages.append(0)
            h2_percentages.append(0)

    # Plotting amounts
    plt.figure(figsize=(10, 5))
    plt.plot(voltage_values, h1_amounts, label=r'$h_1$')
    plt.plot(voltage_values, h2_amounts, label=r'$h_2$')
    plt.xlabel('DC Voltage')
    plt.ylabel('Count')
    plt.legend()
    plt.grid(True)
    plt.show()

    # Plotting percentages
    plt.figure(figsize=(10, 5))
    plt.plot(voltage_values, h1_percentages, label=r'$H_1$')
    plt.plot(voltage_values, h2_percentages, label=r'$H_2$')
    plt.xlabel('DC Voltage')
    plt.ylabel('Percentage (%)')
    plt.legend()
    plt.grid(True)
    plt.show()

# Example usage (assuming 'variables' is your DataFrame):
plot_mc_vs_voltage_constant_count(variables, range_devide=1_000_000)

In [ ]:
variables.plotly_3d_reconstruction.show()

In [ ]:
from IPython.display import display, HTML
display(HTML(variables.animation_detector_html))